## Distribuição Territorial da População

**AUTORIA:** [REDE MOB](https://www.redemob.com.br/)

Este script constrói mapas básicos da área de estudo. Especificamente, serão consolidadas e apresentadas as distribuições territoriais de variáveis demográficas e socioeconômicas de interesse. Adicionalmente, há o complemento de atributos territoriais que entende-se que são, também, variáveis explicativas. Especificamente, o foco estará, preliminarmente, nas seguintes variáveis, as quais serão elaboradas em maior profundidade mais à frente.

- Contagens populacionais
- Rendimentos médios

**PANORAMA:**
- Faz a leitura dos dados do Censo Demográfico: população segundo idade e rendimento
- Produz mapas e gráficos descritivos.


**MAIS INFORMAÇÕES:**
- [Layout da Plataforma]
- [Sumário dos Dados Disponíveis]
- *Lorem ipsum: Conteúdo do MOB de interesse, técnico ou de divulgação*

**LINKS DE INTERESSE:**
- links para materiais técnicos e acadêmicos gerais, externos, de referência a respeito do conteúdo abordado


# Instruções

Este script requer:
1. O código do IBGE para o município
    - Caso se deseje fazer a análise de municípios vizinhos, fornecer uma lista com os códigos do IBGE destes municípios
2. Ano da análise: permite avaliar, alternativamente, dados do Censo de 2010 ou de 2022
    - Para 2022, o Censo apenas liberou dados de rendimento do responsável [até o momento](https://www.ibge.gov.br/novo-portal-destaques/42982-ibge-divulgara-em-30-de-abril-informacoes-do-censo-demografico-2022-sobre-o-rendimento-do-responsavel-pelo-domicilio.html). Com efeito, **não é possível calcular indicadores, como taxa de pobreza e índice de Gini, ou efetuar ranqueamento de divisões territoriais, de acordo com o rendimento**. No entanto, mantivemos a construção de um mapa de população classificado por cores de acordo com o rendimento dos responsáveis por domicílios, pois entendemos que há valor na informação, mas as observações acima devem estar em mente.
  
2. [Chave referente a um projeto no Google Cloud](https://basedosdados.org/docs/access_data_bq)

# Parâmetros Definidos Pelo Usuário

In [14]:
# Backend preliminar
from getpass import getpass

In [15]:
# Forneça código do IBGE da cidade, ou lista de códigos
# se quiser cidades vizinhas. P. ex.:
# ibge_id = 3303302 -> Niterói
ibge_id = [3303302, 3304904, 3301900] # Niterói, São Gonçalo, Itaboraí

# Chave de API do Google Cloud Platform
gcloud_id = getpass("Chave de API do Google Cloud Platform: ")
    

# Backend

## Bibliotecas e Parâmetros Básicos

In [16]:
from io import BytesIO
from pathlib import Path
import requests
import tempfile
import zipfile

from operator import le
import pandas as pd
import geopandas as gpd
from tobler.area_weighted import area_interpolate
from tobler.util import h3fy

import contextily as ctx
import basedosdados as bd
import geobr
import geopandas as gpd
import matplotlib.pyplot as plt
from matplotlib.legend import Legend
from matplotlib.lines import Line2D
from matplotlib_map_utils.core.north_arrow import north_arrow
from matplotlib_scalebar.scalebar import ScaleBar
import mapclassify
import numpy as np
import pandas as pd
import seaborn as sns
from shapely.affinity import scale
from statsmodels.stats.weightstats import DescrStatsW
from tobler.area_weighted import area_interpolate
from tobler.util import h3fy


In [17]:
%matplotlib inline
%config InlineBackend.figure_format = 'retina'
plt.style.use('ggplot')

In [18]:
pd.options.display.float_format = '{:,.2f}'.format

## Área de Estudo

In [19]:
def get_census_tracts(ibge_id, year=2010) -> gpd.GeoDataFrame:
    """
    Prepares the study area by fetching census tracts for the given IBGE IDs.

    Parameters:
        ibge_id (int or list[int]): IBGE municipality code(s).
        year (int): Year of the census data (default is 2010).

    Returns:
        gpd.GeoDataFrame: A GeoDataFrame with census tracts, properly formatted.
    """
    if not isinstance(ibge_id, list):
        ibge_id = [ibge_id]

    # Fetch census tracts for each IBGE ID
    tracts = pd.concat(
        [geobr.read_census_tract(int(id_), year=year) for id_ in ibge_id]
    )
    crs = tracts.estimate_utm_crs(datum_name='SIRGAS 2000')

    # Process and format the GeoDataFrame
    tracts = (
        tracts.astype({'code_tract': np.int64})
        .astype({'code_tract': 'str'})
        .rename(columns={'code_tract': 'id_setor_censitario'})
        .set_index('id_setor_censitario')
        .to_crs(crs)
    )

    return tracts.reindex(columns=['geometry'])

In [20]:
tracts = get_census_tracts(ibge_id)
crs = tracts.estimate_utm_crs(datum_name='SIRGAS 2000')
crs

<Projected CRS: EPSG:31983>
Name: SIRGAS 2000 / UTM zone 23S
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Brazil - between 48°W and 42°W, northern and southern hemispheres, onshore and offshore.
- bounds: (-48.0, -33.5, -42.0, 5.13)
Coordinate Operation:
- name: UTM zone 23S
- method: Transverse Mercator
Datum: Sistema de Referencia Geocentrico para las AmericaS 2000
- Ellipsoid: GRS 1980
- Prime Meridian: Greenwich

# IBEU

Esse é um indicador desenvolvido pelo INCT Observatório das Metrópoles. A métrica 

    procura avaliar a dimensão urbana do bem-estar usufruído pelos cidadãos brasileiros promovido pelo mercado, via o consumo mercantil, e pelos serviços sociais prestados pelo Estado. Tal dimensão está relacionada com as condições coletivas de vida promovidas pelo ambiente construído da cidade, nas escalas da habitação e da sua vizinhança próxima, e pelos equipamentos e serviços urbanos. (Ribeiro & Ribeiro, 2016).

Há cinco dimensões: Mobilidade Urbana, Condições Ambientais Urbanas, Condições Habitacionais Urbanas, Atendimento de Serviços Coletivos Urbanos e Infraestrutura Urbana. Maior detalhamento a respeito das de como é calculada cada uma dessas dimensões podem ser encontrados diretamente em Ribeiro e Ribeiro (2016). Aqui, a exposição se limita a explicar quais dessas dimensões serão utilizadas e por quê.

A dimensão da mobilidade não será utilizada. Essa dimensão tem como principal pilar o tempo de viagem casa-trabalho, tal como capturado pelo Censo de 2010. A variável foca apenas no tempo e, para análise à qual este artigo se propõe, seria necessário um conhecimento mais profundo que envolve, dentre outras, variáveis tais quais (a) pares de origem e destino, (b) modos de viagem — se coletivos ou individuais, p. ex. — e (c) gradientes de acessibilidade ao longo do território. Portanto, essa análise mais minuciosa precisa ser desenvolvida de outra forma, o que será feito em scripts posteriores a partir de pesquisas de origem e destino, dados de GTFS etc.

Outra dimensão que não será utilizada é a de condições habitacionais, pois diz respeito à qualidade física dos domicílios de cada setor e à densidade ocupacional no interior de cada residência. É razoável supor que isso faça pouca diferença para o estabelecimento de empresas ou serviços. Por um lado, locais com baixa condição habitacional podem ser menos atrativos porque tendem a estar em áreas mais periféricas e de menor qualidade urbanística em geral. Por outro, há outras dimensões do IBEU que tratam diretamente da qualidade do espaço público e da qualidade das infraestruturas urbanas existentes. Deve-se ter em mente o seguinte: a hipótese central do artigo é que o estabelecimento de centros comerciais depende do acesso à massa salarial local, acesso esse mediado pelo sistema de transportes. Nesse sentido, pouco importa o que acontece "intramuros", importa o mercado ao qual se tem acesso. Ao cabo, essa variável pode ser vista por dois ângulos: ou como redundante ou como irrelevante.

As demais dimensões serão utilizadas pois elas são entendidas como essenciais à análise em questão. Rememorando, são elas as dimensões (a) de serviços coletivos urbanos, (b) de condições ambientais urbanas e (c) de infraestrutura urbana. A essa altura, já é evidente que o que aqui será produzido é uma versão parcial do IBEU, cujo foco está na forma urbana construída.

Em certa medida,é possível afirmar que também haveria uma correlação importante entre a qualidade do ambiente urbano e os rendimentos do entorno. O que, por um lado, pode levantar suspeitas a respeito da redundância dessa variável. Contudo, entende-se que esse pode ser um critério de desempate interessante, em casos de locais com acesso semelhante. A pertinência dessa variável será demonstrada — ou não — com as análises do modelo.

A respeito da dimensão de serviços coletivos urbanos, Ribeiro e Ribeiro (2016, p. 4) alegam que "esses são indicadores que expressam os serviços públicos essenciais para garantia de bem-estar urbano, independentemente de ser _ofertado por empresas públicas ou por empresas privadas através de concessão pública_ [ênfase adicionada]". Disso, subentende-se que um atendimento adequado estaria refletido pelas seguintes variáveis extraídas da tabela de características gerais dos domicílios:

- v002 : Domicílios particulares e domicílios coletivos

- IBEU Serviços Coletivos Urbanos
    - v012 : Domicílios particulares permanentes com abastecimento de água da rede geral
    - v017 : Domicílios particulares permanentes com banheiro de uso exclusivo dos moradores ou sanitário e esgotamento sanitário via rede geral de esgoto ou pluvial
    - v035 : Domicílios particulares permanentes com lixo coletado
    - v044 : Domicílios particulares permanentes com energia elétrica de companhia distribuidora

As outras duas dimensões são obtidas a partir da tabela com informações a respeito do entorno das quadras dos setores censitários. As variáveis são as seguintes:

- v001 : Domicílios particulares permanentes

- IBEU Infraestrutura Urbana
    - v002 : Domicílios particulares permanentes próprios – Existe identificação do logradouro
    - v004 : Domicílios particulares permanentes alugados – Existe identificação do logradouro
    - v006 : Domicílios particulares permanentes cedidos – Existe identificação do logradouro
    - v008 : Domicílios particulares permanentes próprios – Existe iluminação pública
    - v010 : Domicílios particulares permanentes alugados – Existe iluminação pública
    - v012 : Domicílios particulares permanentes cedidos – Existe iluminação pública
    - v014 : Domicílios particulares permanentes próprios – Existe pavimentação
    - v016 : Domicílios particulares permanentes alugados – Existe pavimentação
    - v018 : Domicílios particulares permanentes cedidos – Existe pavimentação
    - v020 : Domicílios particulares permanentes próprios – Existe calçada
    - v022 : Domicílios particulares permanentes alugados – Existe calçada
    - v024 : Domicílios particulares permanentes cedidos – Existe calçada
    - v026 : Domicílios particulares permanentes próprios – Existe meio-fio/guia
    - v028 : Domicílios particulares permanentes alugados – Existe meio-fio/guia
    - v030 : Domicílios particulares permanentes cedidos – Existe meio-fio/guia
    - v032 : Domicílios particulares permanentes próprios – Existe bueiro/boca-de-lobo
    - v034 : Domicílios particulares permanentes alugados – Existe bueiro/boca-de-lobo
    - v036 : Domicílios particulares permanentes cedidos – Existe bueiro/boca-de-lobo
    - v038 : Domicílios particulares permanentes próprios – Existe rampa para cadeirante
    - v040 : Domicílios particulares permanentes alugados – Existe rampa para cadeirante
    - v042 : Domicílios particulares permanentes cedidos – Existe rampa para cadeirante
        

- IBEU Condições Ambientais Urbanas
    - v044 : Domicílios particulares permanentes próprios – Existe arborização
    - v046 : Domicílios particulares permanentes alugados – Existe arborização
    - v048 : Domicílios particulares permanentes cedidos – Existe arborização
    - v051 : Domicílios particulares permanentes próprios – Não existe esgoto a céu aberto
    - v053 : Domicílios particulares permanentes alugados – Não existe esgoto a céu aberto
    - v055 : Domicílios particulares permanentes cedidos – Não existe esgoto a céu aberto
    - v057 : Domicílios particulares permanentes próprios – Não existe lixo acumulado nos logradouros
    - v059 : Domicílios particulares permanentes alugados – Não existe lixo acumulado nos logradouros
    - v061 : Domicílios particulares permanentes cedidos – Não existe lixo acumulado nos logradouros

Listadas todas as variáveis necessárias, restam algumas notas metodológicas. A cada variável está associado um indicador que diz respeito à proporção de domicílios de cada setor censitário que tem o atributo sendo medido. Por exemplo, se o indicador referente à arborização tiver valor de 0.72, isso significa que 72% dos domicílios daquele setor possuem arborização em seu entorno. Em seguida, o restantante das contas envolve médias aritméticas simples: cada dimensão é representada pela média de seus indicadores constituintes, enquanto  que o IBEU é a média de cada dimensão. Cabe ressaltar outra diferença em relação ao IBEU original: aqui utilizamos como base de cálculo as proporções de domicílios, em vez da proporção de _pessoas_.

    
        Ribeiro, L. C. Q., Ribeiro, M. G. (2016). IBEU-Municipal: Índice de Bem-Estar Urbano dos Municípios Brasileiros. Letra Capital. https://www.observatoriodasmetropoles.net.br/wp-content/uploads/2020/08/ibeumunicipal_2016.pdf

In [108]:
# ---------------------------------------------------------------------
# CONSTANTS
# ---------------------------------------------------------------------

# D2: Environmental Conditions
ENVIRONMENT_GROUPS = {
    'arborizacao': ['v044', 'v046', 'v048'],
    'esgoto': ['v051', 'v053', 'v055'],
    'lixo': ['v057', 'v059', 'v061'],
}

# D4: Collective Urban Services
SERVICES_INDICATORS = ['v012', 'v017', 'v035', 'v044']

# D5: Urban Infrastructure
INFRASTRUCTURE_GROUPS = {
    'logradouro': ['v002', 'v004', 'v006'],
    'iluminacao': ['v008', 'v010', 'v012'],
    'pavimentacao': ['v014', 'v016', 'v018'],
    'calcada': ['v020', 'v022', 'v024'],
    'meio_fio': ['v026', 'v028', 'v030'],
    'bueiro': ['v032', 'v034', 'v036'],
    'rampa': ['v038', 'v040', 'v042'],
}

# D2 + D5: para facilitar as queries
SURROUNDINGS_VARS = (
    ['id_setor_censitario', 'v001'] +
    [f'v{v:03}' for v in range(2, 49, 2)] +
    [f'v{v:03}' for v in range(51, 62, 2)]
)


# ---------------------------------------------------------------------
# UTILITIES
# ---------------------------------------------------------------------

def sql_style_list(sequence):
    """Convert a sequence into a SQL-style list of quoted strings."""
    return ", ".join(f"'{item}'" for item in sequence)


def normalize_min_max(df: pd.DataFrame) -> pd.DataFrame:
    """Normalize DataFrame columns to the [0, 1] interval."""
    return (df - df.min()) / (df.max() - df.min())


def interpolate_to_h3(
    gdf: gpd.GeoDataFrame,
    h3_cells: gpd.GeoDataFrame,
    extensive: list[str],
    intensive: list[str] | None = None,
) -> gpd.GeoDataFrame:
    """Interpolates census data into H3 hexagons using Tobler."""
    return area_interpolate(
        source_df=gdf.fillna(0),
        target_df=h3_cells,
        extensive_variables=extensive,
        intensive_variables=intensive or [],
        allocate_total=True,
    )

# ---------------------------------------------------------------------
# DATA FETCHING
# ---------------------------------------------------------------------

def fetch_urban_services(tracts, gcloud_id):
    """Fetch urban services data from Base dos Dados."""
    query = (
        f"SELECT id_setor_censitario, v002, {', '.join(SERVICES_INDICATORS)} "
        "FROM basedosdados.br_ibge_censo_demografico."
        "setor_censitario_domicilio_caracteristicas_gerais_2010 "
        f"WHERE id_setor_censitario IN ({sql_style_list(tracts.index)})"
    )
    df = bd.read_sql(query, billing_project_id=gcloud_id)
    return tracts.merge(df, left_index=True, right_on='id_setor_censitario')


def fetch_surroundings(tracts, gcloud_id):
    """Fetch surroundings data from Base dos Dados."""
    query = (
        f"SELECT {', '.join(SURROUNDINGS_VARS)} "
        "FROM basedosdados.br_ibge_censo_demografico."
        "setor_censitario_entorno_2010 "
        f"WHERE id_setor_censitario IN ({sql_style_list(tracts.index)})"
    )
    df = bd.read_sql(query, billing_project_id=gcloud_id)
    return tracts.merge(df, left_index=True, right_on='id_setor_censitario')


# ---------------------------------------------------------------------
# DIMENSION SCORE COMPUTATION
# ---------------------------------------------------------------------

def compute_env_score_h3(df: pd.DataFrame) -> pd.Series:
    """Compute D2: Environmental Conditions score."""
    proportions = {
        name: df[cols].sum(axis=1) / df['v001']
        for name, cols in ENVIRONMENT_GROUPS.items()
    }
    normed = normalize_min_max(pd.DataFrame(proportions))
    return normed.mean(axis=1).rename('condicoes_ambientais')


def compute_services_score_h3(df: pd.DataFrame) -> pd.Series:
    """Compute D4: Urban Collective Services score."""
    proportions = df[SERVICES_INDICATORS].div(df['v002'], axis=0)
    normed = normalize_min_max(proportions)
    return normed.mean(axis=1).rename('servicos_coletivos')


def compute_infra_score_h3(df: pd.DataFrame) -> pd.Series:
    """Compute D5: Urban Infrastructure score."""
    proportions = {
        key: df[cols].sum(axis=1) / df['v001']
        for key, cols in INFRASTRUCTURE_GROUPS.items()
    }
    normed = normalize_min_max(pd.DataFrame(proportions))
    return normed.mean(axis=1).rename('infraestrutura_urbana')


# ---------------------------------------------------------------------
# MAIN FUNCTION
# ---------------------------------------------------------------------

def compute_ibeu_h3(
    gdf_surroundings: gpd.GeoDataFrame,
    gdf_services: gpd.GeoDataFrame,
    resolution: int = 9,
) -> pd.DataFrame:
    """
    Compute IBEU scores (D2, D4, D5) per H3 hexagon.

    Parameters
    ----------
    gdf_surroundings : GeoDataFrame
        Census data with infrastructure/environment variables (D2, D5).
    gdf_services : GeoDataFrame
        Census data with collective service variables (D4).
    resolution : int
        H3 resolution level (default: 8).

    Returns
    -------
    pd.DataFrame
        DataFrame with IBEU dimension scores and final IBEU per hex.
    """
    sur_vars = (
        ['v001'] +
        [f'v{v:03}' for v in range(2, 49, 2)] +
        [f'v{v:03}' for v in range(51, 62, 2)]
    )
    serv_vars = ['v002'] + SERVICES_INDICATORS

    h3_cells = h3fy(tracts, resolution=resolution)
    h3_sur = interpolate_to_h3(gdf_surroundings, h3_cells, sur_vars)
    h3_serv = interpolate_to_h3(gdf_services, h3_cells, serv_vars)

    df = h3_sur.drop(columns='geometry').merge(
        h3_serv.drop(columns='geometry'),
        left_index=True,
        right_index=True,
        suffixes=('_env', '_serv')
    )

    scores = pd.concat([
        compute_env_score_h3(h3_sur),
        compute_services_score_h3(h3_serv),
        compute_infra_score_h3(h3_sur)
    ], axis=1)

    scores['ibeu'] = scores.mean(axis=1)
    return h3_cells.merge(scores, left_index=True, right_index=True)


In [77]:
gdf_surroundings=fetch_surroundings(tracts, gcloud_id)
gdf_services=fetch_urban_services(tracts, gcloud_id)

Downloading: 100%|██████████|
Downloading: 100%|██████████|


In [109]:
compute_ibeu_h3(
    gdf_surroundings,
    gdf_services,
).explore('ibeu', cmap='RdYlBu',scheme='UserDefined', tiles='Carto DB positron', classification_kwds={
    'bins': [.5, .700, 0.8, 0.9, 1],
    #'labels': ['Muito Ruim', 'Ruim', 'Médio', 'Bom', 'Muito Bom'],
})

In [96]:
h3fy(tracts, resolution=8)

geometry
hex_id                                                            
88a8a2a40dfffff  POLYGON ((705928.729 7479681.266, 705496.131 7...
88a8a2a5d9fffff  POLYGON ((705666.261 7484168.576, 705146.654 7...
88a8a2ad09fffff  POLYGON ((726969.428 7488006.001, 727055.815 7...
88a8a2aed5fffff  POLYGON ((713111.95 7486295.603, 712679.057 74...
88a8a2b439fffff  POLYGON ((705072.331 7464403.653, 704985.544 7...
...                                                            ...
88a8a2a6c9fffff  POLYGON ((698402.72 7475150.167, 698835.074 74...
88a8a2ac2dfffff  POLYGON ((723937.993 7488638.926, 723504.815 7...
88a8a2a12bfffff  POLYGON ((728087.052 7472464.125, 728606.241 7...
88a8a06919fffff  POLYGON ((694250.903 7473760.726, 693731.544 7...
88a8a06915fffff  POLYGON ((695547.653 7474743.335, 695028.272 7...

[1069 rows x 1 columns]

In [75]:
gdf_services

geometry id_setor_censitario  \
1217  POLYGON ((693454.959 7465557.459, 693397.504 7...     330330205000195   
949   POLYGON ((693397.504 7465619.667, 693363.964 7...     330330205000196   
445   POLYGON ((693419.174 7465709.629, 693465.704 7...     330330205000197   
909   POLYGON ((693363.964 7465656.221, 693260.771 7...     330330205000198   
2460  POLYGON ((693260.771 7465742.727, 693114.911 7...     330330205000199   
...                                                 ...                 ...   
3214  POLYGON ((713909.556 7485051.175, 713652.849 7...     330190040000014   
1650  POLYGON ((712730.911 7486596.418, 712716.74 74...     330190040000015   
3229  POLYGON ((714474.701 7487418.154, 714235.663 7...     330190040000016   
1568  POLYGON ((716658.961 7487577.23, 715746.08 748...     330190040000017   
25    POLYGON ((712521.533 7486783.888, 711248.196 7...     330190040000018   

      v012  v017  v035  v044  
1217   328   326   327   328  
949    112   112   112   112  
445    261   261   261   261  
909    328   328   328   328  
2460   289   290   290   290  
...    ...   ...   ...   ...  
3214     0     0     0    54  
1650  <NA>  <NA>  <NA>  <NA>  
3229    36    34   276   324  
1568     4   107   287   330  
25    <NA>  <NA>  <NA>  <NA>  

[3260 rows x 6 columns]

In [ ]:
import pandas as pd
import numpy as np
import basedosdados as bd

# ---- CONSTANTS ----

# D2
ENV_GROUPS = [
    ['v044', 'v046', 'v048'],  # arborização
    ['v051', 'v053', 'v055'],  # esgoto
    ['v057', 'v059', 'v061'],  # lixo
]

# D4
URBAN_SERVICES_VARS = [
    'id_setor_censitario', 'v002', 'v012', 'v017', 'v035', 'v044'
]

# D5
INFRA_GROUPS = [
    ['v002', 'v004', 'v006'],  # logradouro
    ['v008', 'v010', 'v012'],  # iluminação
    ['v014', 'v016', 'v018'],  # pavimentação
    ['v020', 'v022', 'v024'],  # calçada
    ['v026', 'v028', 'v030'],  # meio-fio
    ['v032', 'v034', 'v036'],  # bueiro
    ['v038', 'v040', 'v042'],  # rampa
]




# ---- UTILS ----

def sql_style_list(sequence):
    """Convert a sequence into a SQL-style list of quoted strings."""
    return ", ".join(f"'{item}'" for item in sequence)

# ---- DATA FETCHING ----

def fetch_urban_services(tracts, gcloud_id):
    """Fetch urban services data from Base dos Dados."""
    query = (
        f"SELECT {', '.join(URBAN_SERVICES_VARS)} "
        "FROM basedosdados.br_ibge_censo_demografico."
        "setor_censitario_domicilio_caracteristicas_gerais_2010 "
        f"WHERE id_setor_censitario IN ({sql_style_list(tracts)})"
    )
    return bd.read_sql(query, billing_project_id=gcloud_id)

def fetch_surroundings(tracts, gcloud_id):
    """Fetch surroundings data from Base dos Dados."""
    query = (
        f"SELECT {', '.join(SURROUNDINGS_VARS)} "
        "FROM basedosdados.br_ibge_censo_demografico."
        "setor_censitario_entorno_2010 "
        f"WHERE id_setor_censitario IN ({sql_style_list(tracts)})"
    )
    return bd.read_sql(query, billing_project_id=gcloud_id)

# ---- GROUPING ----

def sum_groups(df, groups):
    """
    Sum columns in each group for each row.
    Returns a DataFrame with one column per group.
    """
    grouped = {}
    for group in groups:
        name = '-'.join(group)
        grouped[name] = df[group].sum(axis=1)
    return pd.DataFrame(grouped, index=df.index)

def group_surroundings(df):
    """
    Group surroundings DataFrame into infrastructure and environment dimensions.
    Returns two DataFrames: infra, env.
    """
    df = df.set_index('id_setor_censitario')
    infra = sum_groups(df, INFRA_GROUPS)
    env = sum_groups(df, ENV_GROUPS)
    # Add reference column for normalization
    ref = df['v001']
    return infra.assign(v001=ref), env.assign(v001=ref)

# ---- NORMALIZATION ----

def filter_urban(df, ref_col):
    """Filter out tracts with zero or null in the reference column."""
    mask = (df[ref_col] != 0) & df[ref_col].notnull()
    return df.loc[mask]

def normalize_by_reference(df, ref_col):
    """
    Normalize each column by the reference column, dropping the reference.
    """
    df = filter_urban(df, ref_col)
    return (
        df.set_index(df.index)
          .div(df[ref_col], axis=0)
          .drop(columns=ref_col)
    )

# ---- DIMENSION SCORES ----

def compute_urban_services_score(df):
    """Compute mean proportion of each urban service per tract."""
    df = filter_urban(df, 'v002')
    df = df.set_index('id_setor_censitario')
    indicators = ['v012', 'v017', 'v035', 'v044']
    proportions = df[indicators].div(df['v002'], axis=0)
    return proportions.mean(axis=1).rename('servicos_coletivos')

def compute_infra_score(df):
    """Compute mean proportion of each infrastructure attribute per tract."""
    norm = normalize_by_reference(df, 'v001')
    return norm.mean(axis=1).rename('infraestrutura_urbana')

def compute_env_score(df):
    """Compute mean proportion of each environmental attribute per tract."""
    norm = normalize_by_reference(df, 'v001')
    return norm.mean(axis=1).rename('condicoes_ambientais')

# ---- MAIN IBEU FUNCTION ----

def compute_ibeu(tracts, gcloud_id):
    """
    Compute IBEU index for given tracts and Google Cloud project ID.
    Returns a DataFrame with all scores and the final IBEU.
    """
    # Fetch data
    services = fetch_urban_services(tracts, gcloud_id)
    surroundings = fetch_surroundings(tracts, gcloud_id)
    infra, env = group_surroundings(surroundings)

    # Compute scores
    serv_score = compute_urban_services_score(services)
    infra_score = compute_infra_score(infra)
    env_score = compute_env_score(env)

    # Merge all scores
    df = (
        pd.concat([serv_score, infra_score, env_score], axis=1)
          .dropna()
    )
    df['ibeu'] = df.mean(axis=1)
    return df.reset_index()


In [ ]:

# ---- EXAMPLE USAGE ----
# tracts = [...]  # List of id_setor_censitario as strings
# gcloud_id = "your-gcloud-project-id"
# ibeu_df = compute_ibeu(tracts, gcloud_id)
# print(ibeu_df.head())

### IBEU Serviços Coletivos Urbanos

In [ ]:
urban_services_vars = [
    'id_setor_censitario',
    'v002',
    'v012', 
    'v017',
    'v035',
    'v044',
    ]

In [ ]:
query = (
    f"SELECT {', '.join(urban_services_vars)} "
    "FROM basedosdados.br_ibge_censo_demografico.setor_censitario_domicilio_caracteristicas_gerais_2010 "
    f"WHERE id_setor_censitario IN ({_sql_style_list(tracts.code_tract.unique())});"
    )

In [ ]:
services = bd.read_sql(
    query,
    billing_project_id=gcloud_id,
    )

### IBEU Infraestrutura Urbana | Condições Ambientais

In [ ]:
surroundings_vars = (
    ['id_setor_censitario', 'v001']
    + [f'v{v:03}' for v in range(2, 49, 2)]
    + [f'v{v:03}' for v in range(51, 62, 2)]
    )

query = (
    f"SELECT {', '.join(surroundings_vars)} "
    "FROM basedosdados.br_ibge_censo_demografico.setor_censitario_entorno_2010 "
    f"WHERE id_setor_censitario IN ({_sql_style_list(tracts.code_tract.unique())});"
    )

surroundings = bd.read_sql(
    query,
    billing_project_id=gcloud_id,
    )

Os dados dos atributos territoriais fazem uma desagregação por tipo de domicilio. Para o IBEU, essa subdivisão não existe: o que importaa são as residências dotadas de infraestrutura, indpendentemente de serem alugados, cedidos etc. Com efeito, eles serão agrupados, irrespectivamente da situação de posse.

In [ ]:
def _grouping_windows():
    indices = [idx for idx in range(1, surroundings.shape[1]+1, 3)]
    return [(u, v) for u, v in zip(indices[:-1], indices[1:])]


def _wrangle_df(df, u, v):
    sliced_df = df.iloc[:, u:v].copy()
    name = '-'.join(sliced_df.columns)
    return sliced_df.sum(1).rename(name)


def group_surroundings(surroundings):
    windows = _grouping_windows()
    df = surroundings.set_index('id_setor_censitario')
    grouped_df = [
        _wrangle_df(df, u, v)
        for i, (u, v)
        in enumerate(windows)
        ]
    return (
        pd.concat(grouped_df, axis='columns')
          .merge(
              df.v001,
              left_index=True,
              right_index=True,
              ) 
          .reset_index()
        )

In [ ]:
surroundings = group_surroundings(surroundings)

In [ ]:
surroundings.head()

### O Índice

In [ ]:
# Helper functions to compute IBEU

def _urban_area(df, ref_col):
    """Takes only the portion of the dataset
    the is strictly subject to urban dynamics,
    i.e. excludes census tracts of special areas
    such as university campi or penitentiaries.
    
    Parameters
    ----------
    df : DataFrame
        Attributes by census tract
    ref_col : str
        Column containing variable that is either
        zero or null if census tract is a special area
        
    Returns
    -------
        DataFrame
    """
    mask = (df[ref_col] != 0) & df[ref_col].notnull()
    return df.loc[mask]


def _partial_ibeu(partial_data, ref_col):
    df = _urban_area(partial_data, ref_col)
    return (
        df.set_index('id_setor_censitario')
          .pipe(
              lambda df: df.div(df[ref_col], axis='index')
              )
          .drop(columns=ref_col)
        )
    


def compute_ibeu(surroundings, services):
    return (
        pd.merge(
            _partial_ibeu(surroundings, 'v001'),
            _partial_ibeu(services, 'v002'),
            left_index=True,
            right_index=True,
            )
          .apply(lambda row: np.mean(row), axis='columns')
          .rename('ibeu')
        )


In [ ]:
ibeu = compute_ibeu(surroundings, services)

# Os Atributos Territoriais

Resgatando o que foi dito no preâmbulo deste script, estamos interessados nas seguintes variáveis:
1. Contagens populacionais
2. Contagem de domicílios
3. Rendimentos médios

A ideia, portanto, é fazer a leitura e o ajuste dessas variáveis para que possam ser imptuadas nas malhas hexagonais H3.

Deve-se salientar que para 2022, os dados de rendimento médio por setor censitário não estão disponíveis e, por ora, apenas há possibilidade de mapear os rendimentos dos responsáveis pelos domicílios. Embora isso revele insights interessantes, como já dito,**não é possível calcular indicadores, como taxa de pobreza e índice de Gini, ou efetuar ranqueamento de divisões territoriais, de acordo com o rendimento**.

In [96]:
def get_census_tracts(ibge_id, year=2022) -> gpd.GeoDataFrame:
    """
    Prepares the study area by fetching census tracts for the given IBGE IDs.

    Parameters:
        ibge_id (int or list[int]): IBGE municipality code(s).
        year (int): Year of the census data (default is 2022).

    Returns:
        gpd.GeoDataFrame: A GeoDataFrame with census tracts, properly formatted.
    """
    if not isinstance(ibge_id, list):
        ibge_id = [ibge_id]

    # Fetch census tracts for each IBGE ID
    tracts = pd.concat(
        [geobr.read_census_tract(int(id_), year=year) for id_ in ibge_id]
    )
    crs = tracts.estimate_utm_crs(datum_name='SIRGAS 2000')

    # Process and format the GeoDataFrame
    tracts = (
        tracts.astype({'code_tract': np.int64})
        .astype({'code_tract': 'str'})
        .rename(columns={'code_tract': 'id_setor_censitario'})
        .set_index('id_setor_censitario')
        .to_crs(crs)
    )

    return tracts

In [97]:
def import_census_data(year, ibge_id, gcloud_id=None) -> gpd.GeoDataFrame:
    """
    Imports census data for the specified year (2010 or 2022).

    Parameters:
        year (int): The year of the census data (2010 or 2022).
        ibge_id (int, str, iterable): The IBGE municipality codes.
        gcloud_id (str): Google Cloud billing project ID (required for 2010).

    Returns:
        gpd.GeoDataFrame: A GeoDataFrame containing census data with geometry.
    """
    tracts = get_census_tracts(ibge_id, year=year)

    if year == 2010:
        return _import_census_2010(tracts, gcloud_id)
    elif year == 2022:
        return _import_census_2022(tracts, gcloud_id)
    else:
        raise ValueError("Invalid year. Only 2010 and 2022 are supported.")


def _import_census_2010(tracts: gpd.GeoDataFrame, gcloud_id: str) -> pd.DataFrame:
    """
    Imports census data for 2010.

    Parameters:
        gcloud_id (str): Google Cloud billing project ID.

    Returns:
        pd.DataFrame: A DataFrame containing census data for 2010.
    """
    query = (
        "SELECT id_setor_censitario, v009, v002, v001 "
        "FROM basedosdados.br_ibge_censo_demografico.setor_censitario_basico_2010 "
        f"WHERE id_setor_censitario IN ({_sql_style_list(tracts.index)})"
    )

    data = bd.read_sql(query, billing_project_id=gcloud_id)

    data = (
        data
        .astype({"id_setor_censitario": str})
        .rename(
            columns={
                "v009": "rendimento_medio",
                "v002": "habitantes",
                "v001": "domicilios",
            }
        )
    )
    return (
        tracts
        .reindex(columns=['geometry'])
        .merge(
            data,
            how="left",
            left_index=True,
            right_on="id_setor_censitario",
        )
    )


def _import_census_2022(tracts: gpd.GeoDataFrame, gcloud_id: str) -> gpd.GeoDataFrame:
    """
    Imports census data for 2022.

    Parameters:
        tracts (gpd.GeoDataFrame): A GeoDataFrame containing the tracts data.
        gcloud_id (str): Google Cloud billing project ID.

    Returns:
        gpd.GeoDataFrame: A GeoDataFrame containing census data for 2022.
    """
    query = (
        "SELECT id_setor_censitario, pessoas, domicilios, geometria "
        "FROM basedosdados.br_ibge_censo_2022.setor_censitario "
        f"WHERE id_setor_censitario IN ({_sql_style_list(tracts.index)}) "
    )

    data = bd.read_sql(query, billing_project_id=gcloud_id)

    data = gpd.GeoDataFrame(
        data,
        geometry=gpd.GeoSeries.from_wkt(data["geometria"]),
        crs=4326,
    ).drop(columns="geometria").to_crs(31983)

    income_data = get_income_head_household_data()
    return data.merge(
        income_data,
        how="left",
        left_on="id_setor_censitario",
        right_on="id_setor_censitario",
    ).rename(
        columns={'pessoas': 'habitantes'}
    )


def _sql_style_list(sequence):
    """
    Converts a list of values into a SQL-style list of single-quoted strings.
    """
    return ", ".join(f"'{item}'" for item in sequence)


def get_income_head_household_data() -> pd.DataFrame:
    """
    Downloads and processes income data for household heads from the IBGE link.

    Returns:
        pd.DataFrame: A DataFrame with columns 'id_setor_censitario' and
                      'rendimento_medio'.
    """
    url = (
        "https://ftp.ibge.gov.br/Censos/Censo_Demografico_2022/"
        "Agregados_por_Setores_Censitarios_Rendimento_do_Responsavel/"
        "Agregados_por_setores_renda_responsavel_BR_csv.zip"
    )
    print(f"Downloading income data from: {url}")

    response = requests.get(url)
    if response.status_code != 200:
        raise Exception(
            f"Failed to download data. HTTP Status Code: {response.status_code}"
        )

    with zipfile.ZipFile(BytesIO(response.content)) as zf:
        # Search for the CSV file, even if it's in a subdirectory
        csv_file_name = next(
            (name for name in zf.namelist() if name.endswith(".csv")), None
        )
        if not csv_file_name:
            raise FileNotFoundError("No CSV file found in the ZIP archive.")

        with zf.open(csv_file_name) as csv_file:
            income_data = pd.read_csv(csv_file, sep=";", encoding="latin1")

    return (
        income_data
        .rename(
            columns={
                "CD_SETOR": "id_setor_censitario",
                "V06004": "rendimento_medio",
            }
        )
        .reindex(columns=["id_setor_censitario", "rendimento_medio"])
        .astype({"id_setor_censitario": str})
        .replace({"rendimento_medio": {"X": None}})
        .pipe(
            lambda df: df.assign(
                rendimento_medio=(
                    df["rendimento_medio"]
                    .str.replace(",", ".", regex=False)
                    .replace(r"^\.$", None, regex=True)
                    .astype(float)
                )
            )
        )
    )

In [98]:
def get_urban_area_gdf(year: int) -> gpd.GeoDataFrame:
    """
    Given a year (2005, 2015, 2019), download the corresponding ZIP file from IBGE,
    extract the shapefile (even if it's in a subdirectory), and return it as a GeoDataFrame.
    """
    base = (
        "https://geoftp.ibge.gov.br/organizacao_do_territorio/"
        "tipologias_do_territorio/areas_urbanizadas_do_brasil"
    )

    mapping = {
        2005: f"{base}/2005/areas_urbanizadas_do_Brasil_2005_shapes.zip",
        2015: f"{base}/2015/Shapes/AreasUrbanizadasDoBrasil.zip",
        2019: f"{base}/2019/Shapefile/AreasUrbanizadas2019_Brasil.zip",  # confirmed same ZIP name
    }

    closest_key = min(mapping, key=lambda x:abs(x-year))
    #url = mapping[closest_key]
    url = mapping[2019]  # Use the 2019 URL directly for testing
    print(f"Downloading: {url}")
    
    # Stream and extract the ZIP
    response = requests.get(url)
    with zipfile.ZipFile(BytesIO(response.content)) as zf:
        # Create a temporary directory to extract the shapefile
        with tempfile.TemporaryDirectory() as tmpdir:
            tmpdir_path = Path(tmpdir)
            zf.extractall(tmpdir_path)  # Extract all files to the temp directory
            
            # Search for the .shp file recursively
            shp_path = next(tmpdir_path.rglob("*.shp"), None)
            
            if not shp_path:
                raise FileNotFoundError("No .shp file found in the extracted ZIP archive.")
            
            # Read the shapefile using geopandas
            gdf = gpd.read_file(shp_path)

    return gdf

In [99]:
def generate_hexes(tracts, footprint, resolution):
    """
    Generates hexagonal grids (H3) for the given tracts and footprint.

    Parameters:
        tracts (gpd.GeoDataFrame): GeoDataFrame of census tracts.
        footprint (gpd.GeoDataFrame): GeoDataFrame of urban areas.
        resolution (int): H3 resolution level (default is 9).

    Returns:
        gpd.GeoDataFrame: GeoDataFrame of hexagonal grids with spatial join.
    """
    hexes = (
        h3fy(tracts, resolution=resolution)
        .reset_index()
        .sjoin(
            footprint
            .reindex(columns=["geometry"])
            .to_crs(tracts.crs)
            )
        .drop(columns="index_right")
        .drop_duplicates(subset="hex_id")
        .set_index("hex_id")
    )
    return hexes

In [100]:
def interpolate_data_to_hexes(tracts_with_data, hexes):
    """
    Interpolates census data from tracts to hexagonal grids.

    Parameters:
        tracts_with_data (gpd.GeoDataFrame): GeoDataFrame containing census 
            tracts with data.
        hexes (gpd.GeoDataFrame): GeoDataFrame containing hexagonal grids.

    Returns:
        gpd.GeoDataFrame: GeoDataFrame with interpolated data joined to 
            hexagonal grids.
    """
    interpolated_data = area_interpolate(
        source_df=tracts_with_data.assign(geometry=lambda x: x.buffer(0)),
        target_df=hexes,
        extensive_variables=['habitantes', 'domicilios'],
        intensive_variables=['rendimento_medio']
    ).drop(columns='geometry')

    return pd.merge(
        hexes,
        interpolated_data.set_index(hexes.index),
        left_index=True,
        right_index=True
    )

In [101]:
def get_study_area(ibge_id, gcloud_id, year=2022, resolution=9) -> gpd.GeoDataFrame:
    """
    Prepares the study area by fetching census tracts for the given IBGE IDs.

    Parameters:
        ibge_id (int or list[int]): IBGE municipality code(s).
        year (int): Year of the census data (default is 2022).
        gcloud_id (str): Google Cloud billing project ID.
        resolution (int): H3 resolution level (default is 9).

    Returns:
        gpd.GeoDataFrame: A GeoDataFrame with census tracts, properly formatted.
    """
    if not gcloud_id:
        raise ValueError(
            "Google Cloud billing project ID (gcloud_id) is required!"
        )

    # Fetch census tracts for each IBGE ID
    tracts = import_census_data(year, ibge_id, gcloud_id)
    footprint = get_urban_area_gdf(year)
    hexes = generate_hexes(tracts, footprint, resolution)
    interpolated_data = interpolate_data_to_hexes(tracts, hexes)

    return interpolated_data

In [102]:
hexes = get_study_area(ibge_id, gcloud_id, year=ano)

Downloading: 100%|██████████|
Downloading: https://geoftp.ibge.gov.br/organizacao_do_territorio/tipologias_do_territorio/areas_urbanizadas_do_brasil/2019/Shapefile/AreasUrbanizadas2019_Brasil.zip


In [103]:
output_dir = Path().cwd().parent / 'database/1. Socioeconômicos'
output_dir.mkdir(parents=True, exist_ok=True)  # Ensure the directory exists
output_path = output_dir / f'sociodemografia_{ano}.parquet'

hexes.to_parquet(output_path, compression='brotli')

# Visualizações

In [104]:
def classify_income_deciles(
        df,
        income_col='rendimento_medio',
        weight_col='habitantes',
        ):
    """
    Classifies each row into population-weighted income deciles using statsmodels.
    
    Parameters:
        df: pd.DataFrame
        income_col: str - column name with income
        weight_col: str - column name with population weights
    
    Returns:
        pd.Series with decile labels (1–10)
    """
    d = DescrStatsW(df[income_col], weights=df[weight_col])
    # Compute the quantile breakpoints for deciles
    quantiles = [d.quantile(q) for q in np.linspace(0.1, 1.0, 10)]
    bins = [df[income_col].min() - 1] + [float(q) for q in quantiles]
    
    # Assign decile labels 1–10
    return pd.cut(df[income_col], bins=bins, labels=range(1, 11), include_lowest=True)

In [105]:
def plot_socioeconomic_data(
    hexagons: gpd.GeoDataFrame,
    income_col: str,
    population_column: str,
    income_as_decile: bool = True,
    income_scheme: str = "quantiles",
    population_scheme: str = "FisherJenks",
    cmap: str = "RdBu",
    dpi: int = 600,
    output_file: str = None,
):
    """
    Plot hexagons scaled by population and colored by smoothed income.

    Parameters:
        hex_gdf (GeoDataFrame): GeoDataFrame with hexagonal cells.
        income_metric (str): Base name of income column (e.g., 'income').
        population_column (str): Name of population column.
        income_scheme (str): Color classification scheme (e.g., 'quantiles').
        cmap (str): Matplotlib colormap (e.g., 'RdBu').
        dpi (int): Resolution for saved image.
        output_file (str): File path to save image (optional).
    """
    validate_column_exists(hexagons, income_col)
    validate_column_exists(hexagons, population_column)

    hex_gdf = hexagons.query('habitantes > 1')
    if income_as_decile:
        hex_gdf['decil_renda'] = classify_income_deciles(hex_gdf)
        income_col = 'decil_renda'
        income_scheme = None

    fig, ax = setup_plot(hex_gdf)
    plot_hexagons_scaled_by_population(
        hex_gdf, income_col, population_column, income_scheme,
        cmap, ax, population_scheme,
        )
    add_basemap(ax, hex_gdf)
    north_arrow(
        ax, location="upper left", rotation={"crs": hex_gdf.crs, "reference": "center"}
    )
    add_population_legend(ax)
    add_scalebar(ax)
    add_annotations(ax)
    finalize_plot(fig, ax, dpi, output_file)


def plot_hexagons_scaled_by_population(
    hex_gdf, income_col, pop_col, income_scheme, cmap, ax, population_scheme,
):
    """
    Draw hexagons resized by population bin and colored by income.
    """
    values = hex_gdf[pop_col].fillna(0)
   
    classifier_cls = getattr(mapclassify, population_scheme)
    try:
        classifier = classifier_cls(values, k=5)
    except:
        classifier = classifier_cls(values)

    bins = classifier.bins
    bins = np.concatenate([[values.min()], bins])
    
    scales, _ = compute_population_scales_and_labels(bins)
    hex_gdf["_scale"] = pd.cut(
        values, bins=bins, labels=scales, include_lowest=True
    ).astype(float)

    scaled_geom = [
        scale(geom, xfact=s, yfact=s, origin=geom.centroid)
        for geom, s in zip(hex_gdf.geometry, hex_gdf["_scale"])
    ]

    gdf_scaled = gpd.GeoDataFrame(
        hex_gdf[[income_col]].copy(),
        geometry=scaled_geom,
        crs=hex_gdf.crs
    )

    gdf_scaled.plot(
        column=income_col,
        cmap=cmap,
        scheme=income_scheme,
        legend=True,
        edgecolor="none",
        ax=ax,
        legend_kwds={
            "fontsize": 12,
            "title": "Decil de Renda",
            "title_fontsize": 14,
            "frameon": True,  # Enable the frame
            "facecolor": "white",  # Set the frame background color to white
        }
    )
    ax._cached_population_bins = bins


def compute_population_scales_and_labels(bins, scale_min=0.4, scale_max=1.0):
    """
    Given a list of bin edges, compute visual scaling factors and label strings.

    Parameters:
        bins (array-like): Bin edges (length = n_bins + 1)
        scale_min (float): Minimum visual scale factor
        scale_max (float): Maximum visual scale factor

    Returns:
        scales (List[float]): Scaling factors (length = len(bins) - 1)
        labels (List[str]): Formatted bin labels
    """
    n_bins = len(bins) - 1
    scales = np.linspace(scale_min, scale_max, n_bins)
    labels = [
        f"{int(bins[i]):,} – {int(bins[i + 1]):,}"
        for i in range(n_bins)
    ]
    return scales, labels
    

def validate_column_exists(gdf, column):
    if column not in gdf.columns:
        raise ValueError(f"Column '{column}' not found in GeoDataFrame.")


def setup_plot(gdf):
    a4_width = 11.7
    bounds = gdf.total_bounds
    aspect = (bounds[3] - bounds[1]) / (bounds[2] - bounds[0])
    height = a4_width * aspect
    fig, ax = plt.subplots(figsize=(a4_width, height))
    return fig, ax


def add_basemap(ax, gdf):
    ctx.add_basemap(
        ax,
        crs=gdf.crs,
        source=ctx.providers.CartoDB.PositronNoLabels,
    )


def add_scalebar(ax):
    scalebar = ScaleBar(
        dx=1,
        units="m",
        location="lower right",
        scale_loc="bottom",
        box_alpha=0.5
    )
    ax.add_artist(scalebar)


def add_north_arrow(ax):
    ax.annotate(
        "N",
        xy=(0.975, 0.975),
        xytext=(0.975, 0.85),
        arrowprops=dict(
            facecolor="black",
            width=5,
            headwidth=15
        ),
        ha="center",
        va="center",
        fontsize=20,
        xycoords="axes fraction"
    )


def add_scalebar(ax):
    """
    Adds a scalebar to the plot.

    Parameters:
        ax (matplotlib.axes._subplots.AxesSubplot): The Matplotlib axis.
    """
    scalebar = ScaleBar(
        dx=1,
        units="m",
        location="lower right",
        scale_loc="bottom",
        box_alpha=0.5,
    )
    ax.add_artist(scalebar)


def finalize_plot(fig, ax, dpi, output_file):
    ax.axis("off")
    if output_file:
        plt.savefig(output_file, dpi=dpi, bbox_inches="tight")
    else:
        plt.show()
    plt.close(fig)


def add_population_legend(ax, loc="lower right", bbox_to_anchor=(0.995, 0.05)):
    """
    Add a hex size legend using hexagonal markers of varying size.
    """
    bins = getattr(ax, "_cached_population_bins", None)
    scales, labels = compute_population_scales_and_labels(bins)

    # Scale marker size linearly (you may want to fine-tune factor)
    size_factor = 10  # Adjust for visual match
    handles = [
        Line2D(
            [], [],
            marker="h",  # or 'H' for filled hexagon
            color="black",
            linestyle="None",
            markersize=scale * size_factor,
            markerfacecolor="black",
            markeredgewidth=0,
            linewidth=0,
        )
        for scale in scales
    ]

    legend2 = Legend(
        ax,
        handles,
        labels,
        loc=loc,
        bbox_to_anchor=bbox_to_anchor,
        frameon=True,
        fontsize=12,
        title="População Total",
        labelspacing=1.25,
        title_fontsize=14,
        facecolor='white',
    )

    ax.add_artist(legend2)


def _get_places_to_plot():
    muni_by_neighborhood = {
        'Icaraí': 'Niterói',
        'Estrela Do Norte': 'São Gonçalo',
        'Alcântara': 'Alcântara (São Gonçalo)',
        'Itaboraí': 'Itaboraí',
        'Manilha': 'Manilha (Itaboraí)'
    }

    return (
        geobr
        .read_neighborhood()
        .to_crs(31983)
        .query("abbrev_state == 'RJ'")
        .query("name_neighborhood.isin(@muni_by_neighborhood)")
        .replace({'name_neighborhood': muni_by_neighborhood})
        .set_index('name_neighborhood')
        .centroid
        .to_dict()
        )


def add_annotations(ax):
    """
    Add annotations with arrows pointing to municipal seats and Alcântara.

    Parameters:
        ax (matplotlib.axes.Axes): The Matplotlib axis to add annotations to.
        crs (pyproj.CRS or str): The target CRS (e.g., EPSG:31983).
    """
    places = _get_places_to_plot()
    
    # Transform coordinates to the target CRS
    offset = -7000
    for name, coords in places.items():
        x, y = coords.x, coords.y
        ax.annotate(
            name,
            xy=(x, y),  # Coordinates
            xytext=(x, y + offset),  # Offset for text (adjust as needed)
            ha='center',
            arrowprops=dict(
                #arrowstyle="->",
                linewidth=.5,  # Make the arrow thicker
                color="black",
                ),
            fontsize=12,
            color="black",
            bbox=dict(boxstyle="round,pad=0.3", edgecolor="black", facecolor="white"),
        )

        offset *= -1
    



In [106]:
outpath = Path(
    f"../outputs/mapas/sociodemografia_{ano}.png"
    )

In [107]:
plot_socioeconomic_data(
    hexagons=hexes,
    income_col='rendimento_medio',
    population_column="habitantes",
    population_scheme="JenksCaspall",
    cmap="RdYlBu",
    output_file=outpath,
)

# Exercício: Mapas Coropléticos

Objetivo: Compreender os princípios básicos do mapeamento coroplético e aplicar técnicas de classificação e escolha de cores para representar dados espaciais.

Contexto:

Mapas coropléticos são representações cartográficas que utilizam variações de cor para mostrar valores estatísticos agregados por regiões (como estados, municípios ou bairros). Cada região é associada a um valor e preenchida com uma cor que corresponde à sua classe de valor. Embora hoje seja possível criar mapas sem classificação (unclassed), a abordagem com classes (classed) continua sendo valiosa por facilitar a interpretação visual dos dados.

Três decisões fundamentais no mapeamento coroplético:
- Número de classes: Definir em quantos grupos os valores serão divididos.
- Método de classificação: Escolher o algoritmo para agrupar os dados (ex: quantis, intervalos iguais, Jenks).
- Escolha das cores: Aplicar uma paleta que represente adequadamente as diferenças entre os grupos.

Você deve explorar esses conceitos e, para isso, irá utilizar bibliotecas Python como geopandas e [pacotes do conjunto de bibliotecas PySAL](https://pysal.org/). Acompanhe o capítulo Choropleth Mapping do livro [Geographic Data Science with Python](https://geographicdata.science/book/notebooks/05_choropleth.html) e reproduza o exercício prático lá contido com os municípios acima. Documente o passo a passo e discuta e analise seus achados.

# Variação Populacional

In [63]:
hexes = pd.concat([
    get_study_area(ibge_id, gcloud_id, year=y).assign(ano=y)
    for y
    in [2010, 2022]
])

Downloading: 100%|██████████|
Downloading: https://geoftp.ibge.gov.br/organizacao_do_territorio/tipologias_do_territorio/areas_urbanizadas_do_brasil/2019/Shapefile/AreasUrbanizadas2019_Brasil.zip
Downloading: 100%|██████████|
Downloading: https://geoftp.ibge.gov.br/organizacao_do_territorio/tipologias_do_territorio/areas_urbanizadas_do_brasil/2019/Shapefile/AreasUrbanizadas2019_Brasil.zip


In [49]:
def compute_population_change(gdf, year_col='ano', pop_col='habitantes'):
    """
    Computes population change between two years for each hex when hex_id is the index.

    Parameters:
    - gdf: GeoDataFrame with index as hex_id, and columns for year and population.
    - year_col: Column name for year.
    - pop_col: Column name for population.

    Returns:
    - GeoDataFrame with population change and geometry per hex_id.
    """
    # Reset index to ensure hex_id is included in pivot
    gdf_reset = gdf.reset_index()

    # Pivot: rows = hex_id, columns = year, values = population
    pivot = gdf_reset.pivot_table(index=gdf.index.name, 
                                   columns=year_col, 
                                   values=pop_col)

    # Validate year count
    if pivot.shape[1] != 2:
        raise ValueError("Data must contain exactly two years for comparison.")
    
    # Compute signed difference
    years = sorted(pivot.columns)
    pivot['Variação Populacional'] = pivot[years[1]].sub(pivot[years[0]], fill_value=0)

    # Add back geometry
    geometry = gdf[~gdf.index.duplicated(keep='first')]['geometry']
    result = pivot[['Variação Populacional']].join(geometry)

    return gpd.GeoDataFrame(result, geometry='geometry').dropna()


In [73]:
pop_delta = compute_population_change(hexes)

outpath = Path(
    f"../outputs/mapas/variacao_populacional.png"
    )

fig, ax = setup_plot(pop_delta)
pop_delta.plot(
    column='Variação Populacional',
    cmap='PiYG',
    scheme='StdMean',
    legend=True,
    edgecolor="none",
    ax=ax,
    legend_kwds={
        "fontsize": 12,
        "title": "Variação Populacional",
        "title_fontsize": 14,
        "frameon": True,  # Enable the frame
        "facecolor": "white",  # Set the frame background color to white
    }
)

add_basemap(ax, pop_delta)
north_arrow(
    ax, location="upper left", rotation={"crs": pop_delta.crs, "reference": "center"}
)
add_scalebar(ax)
add_annotations(ax)
finalize_plot(fig, ax, 600, output_file=outpath)

In [67]:
hexes.groupby('ano').agg({
    'habitantes': 'sum'
})

habitantes
ano              
2010 1,698,264.00
2022 1,602,211.00

In [69]:
481_749 + 896_744 +224_267 

1602760

In [71]:
218_008 + 487_562 + 999_728 

1705298